# A Guide to TF Layers: Building a Convolutional Neural Network

高レベルAPIである`layers`モジュールを使うとニューラルネットワークを簡単に作れる．

## Intro to Convolutional Neural Networks
CNNは3つの要素を含んでいる．
Convolutional layers, Pooling layers, Dense layersの3つ．

### Convolutional layers
特定の数のフィルタを画像に対して適用するレイヤ．
各サブ領域にて，数学的な操作を実行して，出力するfeature mapにおける一画素の値を計算する．
Convolutional layersは一般的にはその出力に対して`ReLU activation function`を適用して，モデルに非線形関数を導入する．

### Pooling layers
Convolutional layerから抽出された画像データをダウンサンプルして，特徴マップの次元を削減するレイヤ．
よく使われるPoolingアルゴリズムはmax poolingである．
max poolingは特徴マップにおけるサブ領域(例えば2x2ピクセルタイル)の中での，最大値を保持して，その他の全値を捨てる．

### Dense (fully connected) layers
Convolutional layerとPooling layerによって抽出された特徴の分類を行うレイヤ．
レイヤ中の全ノードは，前レイヤの全ノードと結合している．


一般的なCNNは特徴抽出を行うconvolutionalモジュールの積み重ねで構成されており，各モジュールはpooling layerをつけたconvolutional layerで構成されている．
最後のconvolutionalモジュールには分類を行うための1つ以上のdense layersが付いている．
その最後のdense layerは，各ノードが0-1の値を出力するように`softmax`活性化関数を使って，各ターゲットに対して1つのノードを保有している．

## Building the CNN MNIST Classifier
CNNアーキテクチャに従って，MNISTの画像分類モデルを構築する．
1. Convolutional Layer #1
    - ReLU活性化関数を使って32の5x5フィルタを適用する．
2. Pooling Layer #1
    - 2x2のフィルタでmax poolingを実行する．strideは2(pooled regionは重なり無し)とする．
3. Convolutional Layer #2
    - ReLU活性化関数を使って64の5x5フィルタを適用する．
4. Pooling Layer #2
    - Pooling Layer #1と同様．
5. Dense Layer #1
    - 1024ニューロン．dropout正規化のレートは0.4とする．
    - 0.4の確率によって，全ての要素が学習の間にdropped(欠落)される．
6. Dense Layer #2
    - 10ニューロン．0-9の数字(ターゲット)を分類するため．


In [5]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

# Imports
import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)

# Our application logic will be added here
def cnn_model_fn(features, labels, mode):
    """Model function for CNN."""
    # Input Layer
    input_layer = tf.reshape(features["x"], [-1,28,28,1])
    
    # Convolutional Layer #1
    conv1 = tf.layers.conv2d(
        inputs = input_layer,
        filters = 32,
        kernel_size=[5,5],
        padding="same",
        activation = tf.nn.relu
    )
    
    # Pooling Layer #1
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2,2], strides=2)
    
    # Convolutional Layer #2 and Pooling Layer #2
    conv2 = tf.layers.conv2d(
        inputs = pool1,
        filters = 64,
        kernel_size=[5,5],
        padding="same",
        activation = tf.nn.relu
    )
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2,2], strides=2)
    
    # Dense Layer
    pool2_flat = tf.reshape(pool2, [-1, 7*7*64])
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)
    
    # Logits Layer
    logits = tf.layers.dense(inputs=dropout, units=10)
    
    
    predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }
    

    if  mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)
    
    # Calculate Loss (for both TRAIN and EVAL modes)    
    onehot_labels = tf.one_hot(indices=tf.cast(labels, tf.int32), depth=10)
    loss = tf.losses.softmax_cross_entropy(onehot_labels=onehot_labels, logits=logits)

    # Configure the Training Op (for TRAIN mode)
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(
            loss=loss,
            global_step = tf.train.get_global_step()
        )
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)
    
    # Add evaluation metrics (for EVAL mode)
    eval_metric_ops = {
        "accuracy": tf.metrics.accuracy(
        labels=labels, predictions=predictions["classes"])
    }
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


def main(unused_argv):
    # Load training and eval data
    mnist = tf.contrib.learn.datasets.load_dataset("mnist")
    train_data = mnist.train.images # Returns np.array
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images # Returns np.array
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
    
    # Create the Estimator
    mnist_classifier = tf.estimator.Estimator(
    model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")
    
    # Set up logging for predictions
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)
    
    # Train the model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": train_data},
        y=train_labels,
        batch_size=100,
        num_epochs=None,
        shuffle=True)
    mnist_classifier.train(
        input_fn=train_input_fn,
        steps=20000,
        hooks=[logging_hook])
    
    
    # Evaluate the model and print results
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(
        x={"x": eval_data},
        y=eval_labels,
        num_epochs=1,
        shuffle=False)
    eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
    print(eval_results)

if __name__ == "__main__":
  tf.app.run()

Extracting MNIST-data\train-images-idx3-ubyte.gz
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Extracting MNIST-data\t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_log_step_count_steps': 100, '_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': 1, '_keep_checkpoint_max': 5, '_save_summary_steps': 100, '_keep_checkpoint_every_n_hours': 10000, '_session_config': None, '_save_checkpoints_secs': 600, '_save_checkpoints_steps': None}
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Saving checkpoints for 1 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:probabilities = [[ 0.10120953  0.11105895  0.08164095  0.10795659  0.10076244  0.09121952
   0.09025645  0.09915902  0.0996861   0.11705044]
 [ 0.08729999  0.11371092  0.07049035  0.12262191  0.10905834  0.09727554
   0.10641873  0.08342689  0.10330445  0.10639285]
 [ 0.09790797  0.10682889  0.10039324  0.10498559

INFO:tensorflow:loss = 2.30587, step = 1
INFO:tensorflow:probabilities = [[ 0.09990618  0.10786386  0.08505924  0.10865611  0.09714318  0.09246758
   0.10334674  0.10286003  0.09447028  0.10822681]
 [ 0.07721392  0.11279935  0.08444573  0.10053122  0.11997268  0.09535188
   0.09583034  0.0831084   0.11594841  0.114798  ]
 [ 0.09181788  0.12188115  0.09966885  0.09457305  0.10343154  0.0929151
   0.09556104  0.07027414  0.10152474  0.12835248]
 [ 0.09721328  0.11127835  0.08397806  0.11063691  0.10447231  0.08195035
   0.11705708  0.09522107  0.09446903  0.10372351]
 [ 0.08630401  0.11472682  0.08733633  0.10335489  0.10807516  0.09910083
   0.11477587  0.07896986  0.09389624  0.11346008]
 [ 0.105451    0.10960737  0.08588734  0.09576865  0.10597254  0.09092207
   0.09491181  0.10822173  0.0966813   0.10657618]
 [ 0.09514526  0.10959245  0.09506015  0.10649649  0.08735783  0.07885689
   0.1077987   0.11733712  0.08750983  0.11484516]
 [ 0.08271982  0.09903344  0.0778744   0.10265768  0.

INFO:tensorflow:global_step/sec: 162.188
INFO:tensorflow:probabilities = [[ 0.10612267  0.10435825  0.10288409  0.10456927  0.09452506  0.094312
   0.10158959  0.09048632  0.09276383  0.10838893]
 [ 0.09616297  0.10052063  0.0858211   0.10787151  0.10135841  0.08418965
   0.11001831  0.10870689  0.09221017  0.11314036]
 [ 0.11436196  0.09331111  0.08985363  0.1155129   0.09113684  0.09477017
   0.10486521  0.09578226  0.09645126  0.1039546 ]
 [ 0.0887287   0.10730558  0.10066289  0.10271938  0.10735066  0.08248065
   0.11093631  0.08448545  0.09491475  0.12041565]
 [ 0.11234243  0.11388052  0.09029397  0.11140857  0.09999529  0.09518111
   0.09513673  0.10469245  0.0783374   0.09873156]
 [ 0.08891945  0.11293761  0.08838881  0.12039595  0.10156035  0.09313594
   0.10491592  0.10250064  0.08581055  0.10143485]
 [ 0.07763359  0.10366917  0.0832504   0.10226819  0.10950545  0.10825337
   0.10066897  0.09324048  0.10586435  0.11564596]
 [ 0.10559149  0.10471176  0.08514524  0.11713366  0.0

INFO:tensorflow:loss = 2.28834, step = 101 (0.618 sec)
INFO:tensorflow:probabilities = [[ 0.08472645  0.11065966  0.08358919  0.10581593  0.10230158  0.10738338
   0.10885335  0.0800233   0.10528887  0.11135827]
 [ 0.08944498  0.10997158  0.08881485  0.10809167  0.09569824  0.09608375
   0.10840236  0.09824146  0.09740415  0.10784702]
 [ 0.09647132  0.10655393  0.09501097  0.08966076  0.10061377  0.09813407
   0.10798409  0.09360615  0.10627265  0.10569222]
 [ 0.09663364  0.10652126  0.08641108  0.11107598  0.09690302  0.08596971
   0.10574291  0.09287382  0.09775212  0.12011653]
 [ 0.09643818  0.10033253  0.09988444  0.10690355  0.09817827  0.0820143
   0.11774786  0.08465265  0.10426749  0.10958073]
 [ 0.08872411  0.10825896  0.0892163   0.11363279  0.09419619  0.07732765
   0.09632886  0.09702664  0.12204126  0.11324726]
 [ 0.09030093  0.10456923  0.08885866  0.10183074  0.10167902  0.09291992
   0.11262839  0.09639185  0.11233312  0.09848818]
 [ 0.09502155  0.10758528  0.08931699  

INFO:tensorflow:global_step/sec: 159.435
INFO:tensorflow:probabilities = [[ 0.08739983  0.11240661  0.08926824  0.11186396  0.10642289  0.08944856
   0.08676443  0.09725317  0.10887022  0.11030211]
 [ 0.08725691  0.11024089  0.07816879  0.08859829  0.11385121  0.10065534
   0.11716158  0.09969339  0.10086906  0.10350452]
 [ 0.11679122  0.09631915  0.08974595  0.10874024  0.09628944  0.09725657
   0.10528418  0.09026937  0.09689943  0.10240434]
 [ 0.08946742  0.10102648  0.09519149  0.10534342  0.10768651  0.09398415
   0.1042885   0.0999018   0.1011612   0.10194901]
 [ 0.09067392  0.10758409  0.08878876  0.11947622  0.09716957  0.10618342
   0.10904533  0.08075754  0.09945486  0.10086637]
 [ 0.09826641  0.10728925  0.0948609   0.10159913  0.09808359  0.08527065
   0.1069315   0.09781729  0.10004096  0.10984036]
 [ 0.09804163  0.10616866  0.10113551  0.10363545  0.08819912  0.09851468
   0.10134     0.0984968   0.09666753  0.10780059]
 [ 0.10449316  0.10638743  0.08569439  0.1072161   0

...

INFO:tensorflow:global_step/sec: 168.135
INFO:tensorflow:probabilities = [[ 0.00082523  0.98272979  0.00037251  0.00341974  0.00091269  0.00022248
   0.00016722  0.00835503  0.00083195  0.00216327]
 [ 0.00000106  0.00000081  0.00000247  0.00024933  0.          0.00001698
   0.          0.99969089  0.00000038  0.00003814]
 [ 0.00249081  0.00000331  0.00759221  0.00002727  0.05867774  0.00016548
   0.93073982  0.00000837  0.00025105  0.00004397]
 [ 0.00000003  0.00001622  0.00167783  0.99826425  0.00000001  0.00000784
   0.00000157  0.          0.00003198  0.00000019]
 [ 0.00043983  0.00017058  0.00592452  0.00002254  0.02729834  0.00016799
   0.96530426  0.000029    0.00044402  0.0001988 ]
 [ 0.04700672  0.00176213  0.01286586  0.79678553  0.00174571  0.09563158
   0.00106446  0.00633754  0.00697437  0.02982609]
 [ 0.00001337  0.99856144  0.00006484  0.00024799  0.00012568  0.00001623
   0.00003589  0.00068032  0.00017614  0.0000781 ]
 [ 0.00000329  0.18354821  0.0003945   0.00990795  0

INFO:tensorflow:loss = 0.130063, step = 19901 (0.604 sec)
INFO:tensorflow:probabilities = [[ 0.00011287  0.00001724  0.00266983  0.31762347  0.00003367  0.12411989
   0.00002424  0.00002845  0.54820937  0.00716105]
 [ 0.00060535  0.00239025  0.77780116  0.12923542  0.00000025  0.00048413
   0.00000763  0.00000341  0.08947115  0.00000122]
 [ 0.00000011  0.00001697  0.00309804  0.99403739  0.00001522  0.00000155
   0.00000004  0.00064519  0.0019596   0.00022596]
 [ 0.00000261  0.00001907  0.00002068  0.0000883   0.99712002  0.00002104
   0.00007469  0.00115696  0.00030809  0.00118862]
 [ 0.15178604  0.02735369  0.01141799  0.37327355  0.0002644   0.01618662
   0.41521382  0.00016965  0.00426959  0.00006452]
 [ 0.00017904  0.00009415  0.00003461  0.06343372  0.00001373  0.91818118
   0.00000332  0.01299253  0.00078376  0.00428403]
 [ 0.00260345  0.00197057  0.0005416   0.00048238  0.05104664  0.01066244
   0.92501807  0.00005743  0.00726728  0.00035006]
 [ 0.00000335  0.9983741   0.000014

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:Loss for final step: 0.0307925.
INFO:tensorflow:Starting evaluation at 2017-10-02-15:14:29
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model\model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2017-10-02-15:14:30
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9698, global_step = 20000, loss = 0.103186
{'loss': 0.10318608, 'global_step': 20000, 'accuracy': 0.9698}


SystemExit: 

C:\Users\ognek\AppData\Local\conda\conda\envs\tensorflow\lib\site-packages\IPython\core\interactiveshell.py:2870: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
